In [4]:
#Programe

#Imports
import collections
from ortools.sat.python import cp_model
import plotly.figure_factory as ff
import pandas as pd

#Start time for visualization
plan_date = pd.to_datetime('12/07/2021 18:00:00')


#Visualisation function
def visualize_schedule(assigned_jobs,all_staffs,plan_date):
    final = []
    for staff in all_staffs:
        assigned_jobs[staff].sort()
        for assigned_task in assigned_jobs[staff]:
            name = 'Order_%i' % assigned_task.job
            temp = dict(Task=staff,Start=plan_date + pd.DateOffset(minutes = assigned_task.start),
                        Finish= plan_date + pd.DateOffset(minutes = (assigned_task.start + assigned_task.duration)),
                        Resource=name)
            final.append(temp)
    final.sort(key = lambda x: x['Task'])
    return final

#Function
def Minimalizace_casovych_prodlev():
    global job_id, task_id, task

#model
    model = cp_model.CpModel() #CP model

#Import
    zakazky = [
        [(2, 3, ()), (0, 7, (0,)), (1, 17, (1,)), (0, 5, ()), (2, 16, (3,)), (1, 12, (4,)), (0, 5, ()), (1, 3, (6,)), (2, 4, (7,)), (2, 14, (2, 5, 8)), (1, 8, (9,)), (0, 0, (10,))], # zakázka 0
        [(1, 7, ()), (0, 4, ()), (3, 1, (1,)), (2, 6, (2,)), (4, 1, (3,)), (1, 8, (4,)), (2, 16, (0, 5)), (1, 7, (6,)), (0, 0, (7,))] # zakázka 1
    ]

#data definition
    pocet_stroju = 1 + max(task[0] for job in zakazky for task in job) #number of machines
    vsechny_stroje = range(pocet_stroju)  #range of machines
    horizont = sum(task[1] for job in zakazky for task in job) #Max time
    

#definition variables
    task_type = collections.namedtuple('task_type', 'start end interval')
    assigned_task_type = collections.namedtuple('assigned_task_type', 'start job index duration')
    #print('task_type', task_type)
    #print('assigned_task_type', assigned_task_type)
    all_tasks = {}
    machine_to_intervals = collections.defaultdict(list)
    #print('all_tasks', all_tasks)
    #print('machine_to_intervals', machine_to_intervals)
    for job_id, job in enumerate(zakazky):
        for task_id, task in enumerate(job):
            #print(job_id)
            #print(job)
            #print(task_id)
            #print(task)
            machine = task[0]
            duration = task[1]
            suffix = '_%i_%i' % (job_id, task_id)
            start_var = model.NewIntVar(0, horizont, 'start' + suffix)
            end_var = model.NewIntVar(0, horizont, 'end' + suffix)
            interval_var = model.NewIntervalVar(start_var, duration, end_var,
                                                'interval' + suffix)
            all_tasks[job_id, task_id] = task_type(start=start_var,
                                                   end=end_var,
                                                   interval=interval_var)
            machine_to_intervals[machine].append(interval_var)
            #print('start_var', start_var)
            #print('end_var', end_var)
            #print('machine', machine)
            #print('duration', duration)
            #print('suffix', suffix)
            #print('interval_var', interval_var)
            #print('all_tasks', all_tasks)

#definition limitations
    #no over lap
    for machine in vsechny_stroje:
        model.AddNoOverlap(machine_to_intervals[machine])

    #sequence
    for job_id, job in enumerate(zakazky):
        for task_id in range(len(job) - 1):
            for SerialNumber in job[task_id][2]:
                model.Add(all_tasks[job_id, SerialNumber].end <= all_tasks[job_id, task_id].start)

#definition outputs
    obj_var = model.NewIntVar(0, horizont, 'makespan')
    print('obj_var', obj_var)
    model.AddMaxEquality(obj_var, [
        all_tasks[job_id, len(job) - 1].end
        for job_id, job in enumerate(zakazky)
    ])

    model.Minimize(obj_var)

    solver = cp_model.CpSolver()
    status = solver.Solve(model)

#results
    if status == cp_model.OPTIMAL:
        # Create one list of assigned tasks per machine
        assigned_jobs = collections.defaultdict(list)
        for job_id, job in enumerate(zakazky):
            for task_id, task in enumerate(job):
                machine = task[0]
                assigned_jobs[machine].append(
                    assigned_task_type(start=solver.Value(
                        all_tasks[job_id, task_id].start),
                        job=job_id,
                        index=task_id,
                        duration=task[1]))

        # Create per machine output lines
        output = ''
        for machine in vsechny_stroje:
            # Sort by starting time...
            assigned_jobs[machine].sort()
            sol_line_tasks = 'Machine ' + str(machine) + ': '
            sol_line = '           '

            for assigned_task in assigned_jobs[machine]:
                name = 'job_%i_%i' % (assigned_task.job, assigned_task.index)
                # Add spaces to output to align columns
                sol_line_tasks += '%-10s' % name

                start = assigned_task.start
                duration = assigned_task.duration
                sol_tmp = '[%i,%i]' % (start, start + duration)
                # Add spaces to output to align columns
                sol_line += '%-10s' % sol_tmp

            sol_line += '\n'
            sol_line_tasks += '\n'
            output += sol_line_tasks
            output += sol_line

        # Finally print the solution found
        print('Optimal Schedule Length: %i' % solver.ObjectiveValue())
        #print(output)
    res = visualize_schedule(assigned_jobs,vsechny_stroje,plan_date)
    fig = ff.create_gantt(res, index_col='Resource', show_colorbar=True, group_tasks=True)
    fig.show()

Minimalizace_casovych_prodlev()

obj_var makespan
Optimal Schedule Length: 0
